In [7]:
import pandas as pd
import numpy as np
import geojson
import folium
import bs4

# 데이터 불러오기

In [8]:
# 그물망 좌표
df_id = pd.read_csv("dg_points_cor.csv", encoding = 'UTF-8')
df_id

id       cor_x      cor_y
0      10023  128.488251  35.900443
1      10023  128.491573  35.900401
2      10023  128.491522  35.897699
3      10023  128.488200  35.897740
4      10023  128.488251  35.900443
...      ...         ...        ...
50925   9952  128.480012  35.635600
50926   9952  128.483323  35.635559
50927   9952  128.483273  35.632856
50928   9952  128.479962  35.632897
50929   9952  128.480012  35.635600

[50930 rows x 3 columns]

In [9]:
# 피복도 성분들
df_mesh = pd.read_csv("dg_result_mesh300_5186.csv", encoding = 'EUC-KR')
df_mesh

id  L1_CODE L1_NAME  L2_CODE L2_NAME  L3_CODE L3_NAME         area
0       11626      300    산림지역      310    활엽수림      311    활엽수림   3985.14574
1       11626      300    산림지역      310    활엽수림      311    활엽수림  13927.47360
2       11626      300    산림지역      320    침엽수림      321    침엽수림     10.98206
3       11626      300    산림지역      320    침엽수림      321    침엽수림   1329.77293
4       11626      300    산림지역      320    침엽수림      321    침엽수림    398.51988
...       ...      ...     ...      ...     ...      ...     ...          ...
297064  11705      400      초지      420    인공초지      423    기타초지     28.82615
297065  11705      600      나지      620    인공나지      623    기타나지   6961.69782
297066  11705      300    산림지역      320    침엽수림      321    침엽수림   3618.26696
297067  11705      300    산림지역      320    침엽수림      321    침엽수림    381.99494
297068  11705      400      초지      420    인공초지      423    기타초지    905.50025

[297069 rows x 8 columns]

# 그물망 id마다 좌표정리

In [10]:
e = {}
IDs = set()
for index, row in df_id.iterrows():
    IDs.add(int(row['id']))
    newdict = {row['id'] : [[row['cor_x'], row['cor_y']]]}
    if row['id'] in e :
        now = e[row['id']]
        newelem = [row['cor_x'], row['cor_y']]
        now.append(newelem)
        e.update({row['id'] : now})
    else :
        e.update(newdict)

IDs = list(IDs)

# 그물망 id마다 토지피복도 성분 정리

In [11]:
df_pibok = pd.DataFrame()

for ID in IDs :
    df_temp = df_mesh.loc[df_mesh['id'] == ID]
    arr_temp = list()
    for num in np.arange(100, 701, 100) :
        arr_temp.append(df_temp.loc[df_mesh['L1_CODE'] == num]['area'].sum())
    arr_temp = list(arr_temp/sum(arr_temp))
    arr_temp.insert(0,ID)
    df_pibok = df_pibok.append(pd.DataFrame(arr_temp).T)

df_pibok.set_axis(['id', 'used_area', 'agri_land', 'forest', 'grass', 'wet_land', 'barren', 'water'], axis = 'columns', inplace = True)
df_pibok.set_index('id', verify_integrity=True, inplace = True)
#     df_pibok = df_pibok.append({ID : list(arr_temp)}, ignore_index=True)

In [12]:
df_pibok

used_area  agri_land    forest     grass  wet_land    barren  \
id                                                                      
3335.0    0.083884   0.019356  0.015335  0.136398  0.000000  0.054373   
3336.0    0.000000   0.000000  0.000000  0.222666  0.000000  0.000000   
3337.0    0.000000   0.000000  0.000000  0.725686  0.000000  0.000000   
3338.0    0.000000   0.000000  0.000000  0.797091  0.000000  0.002684   
3339.0    0.000000   0.000000  0.000000  0.645984  0.018724  0.003323   
...            ...        ...       ...       ...       ...       ...   
23884.0   0.017516   0.390214  0.402951  0.155495  0.014975  0.007869   
23885.0   0.025754   0.259267  0.364629  0.119146  0.002692  0.033040   
23886.0   0.021571   0.082018  0.840943  0.052670  0.000000  0.002550   
23888.0   0.289011   0.490654  0.000000  0.153471  0.004318  0.059813   
23889.0   0.149716   0.682327  0.000000  0.088884  0.041605  0.037468   

            water  
id                 
3335.0   0.690655  
3336.0   0.777334  
3337.0   0.274314  
3338.0   0.200225  
3339.0   0.331970  
...           ...  
23884.0  0.010980  
23885.0  0.195473  
23886.0  0.000249  
23888.0  0.002732  
23889.0  0.000000  

[10186 rows x 7 columns]

# 토지피복도에서 가장 많은 성분을 토대로 지도 제작 예시

In [13]:
def meshcolor(ID) :
    mostpart = df_pibok.loc[ID].idxmax(axis=1)
    colormap = {'used_area' :'#ff0000' ,
        'agri_land' :'#eeea07' ,
        'forest' :'#2a4b2d' ,
        'grass' :'#399926' ,
        'wet_land' :'#7c227e' ,
        'barren' :'#59ceca' ,
        'water' : '#0602fa' }
    return colormap.get(mostpart, '#000000')

In [14]:
from geojson import Feature, Point, Polygon, FeatureCollection

my_features = []
my_keys = []
for x in e:
    my_features.append(Feature(id = x, geometry=Polygon([e[x]]), properties = {'color' : meshcolor(x)}))
    my_keys.append([x, np.random.rand()])
    
myFeatureCollection = FeatureCollection(my_features)

In [24]:
with open('dg_feature_collection.geojson', 'w') as f:
    geojson.dump(myFeatureCollection, f)

In [15]:
my_data = pd.DataFrame(my_keys, columns = ['id', 'color'])
my_data

id     color
0      10023.0  0.603361
1      10024.0  0.065588
2      10025.0  0.106755
3      10026.0  0.397777
4      10027.0  0.969815
...        ...       ...
10181   9948.0  0.974771
10182   9949.0  0.301382
10183   9950.0  0.898102
10184   9951.0  0.586912
10185   9952.0  0.970374

[10186 rows x 2 columns]

In [17]:
m = folium.Map(location=[35.8714, 128.6014], zoom_start = 12)

folium.GeoJson(
    myFeatureCollection,
    style_function = lambda feature: {
        'fillcolor' : 'black' ,
        'color' : feature['properties']['color'],
        'weight' : 1,
        'dasyArray' : '5, 3'
    }
).add_to(m)

m

In [18]:
m.save('daegu_grid_pibok.html')

In [39]:
# 초단기 예보 오늘 (base_date) 최근 1일만 제공!!
from urllib.request import Request, urlopen
from urllib.parse import urlencode, quote_plus
from bs4 import BeautifulSoup


url = 'http://apis.data.go.kr/1360000/VilageFcstInfoService_2.0/getUltraSrtFcst'
my_key = 'Fg0fw4UiX52kviKPZhe3aLRjwmchaDRbtdzLwSroS27BEVspr3mcXvaaHjbqR0J22i8MYHptv%2FyPaN0B%2FY86yQ%3D%3D'.encode('utf-8')

queryParams = '?' + urlencode({ quote_plus('ServiceKey') : my_key, 
                               quote_plus('numOfRows') : 100, 
                               quote_plus('pageNo') : 1, 
                               quote_plus('dataType') : 'XML', 
                               quote_plus('base_date') : 20210815, 
                               quote_plus('base_time') : '0630', 
                               quote_plus('nx') : 35, 
                               quote_plus('ny') : 128})
    
request = Request(url + unquote(queryParams))
request.get_method = lambda: 'GET'
response_body = urlopen(request).read()
# print(response_body)
xmlobj = bs4.BeautifulSoup(response_body, 'lxml-xml')
items = xmlobj.findAll('item')
asos = pd.DataFrame()
    
for i in items:
    dic_ = {}
    for j in i.find_all():
        dic_[j.name] = [j.text]
    asos = pd.concat([asos, pd.DataFrame(dic_)],axis=0)

In [40]:
def func(row):
    if row['category'] == 'T1H':
        return 'temp'
    elif row['category'] == 'RN1':
        return 'rainfall'
    elif row['category'] == 'REH':
        return 'humi'
    elif row['category'] == 'WSD':
        return 'wind'
    else :
        return ''
    
asos['category'] = asos.apply(func, axis = 1)   

In [41]:
asos.loc[(asos['fcstTime'] == '0700') & (asos['category'] != '')]

baseDate baseTime  category  fcstDate fcstTime fcstValue  nx   ny
0  20210815     0630  rainfall  20210815     0700    1mm 미만  35  128
0  20210815     0630      temp  20210815     0700        24  35  128
0  20210815     0630      humi  20210815     0700        80  35  128
0  20210815     0630      wind  20210815     0700         7  35  128

In [316]:
from urllib.parse import unquote

unquote(queryParams)

'?ServiceKey=Fg0fw4UiX52kviKPZhe3aLRjwmchaDRbtdzLwSroS27BEVspr3mcXvaaHjbqR0J22i8MYHptv%2FyPaN0B%2FY86yQ%3D%3D&numOfRows=100&pageNo=1&dataType=XML&base_date=20210813&base_time=0630&nx=35&ny=128'